In [1]:
import itertools as it
import collections as cl

## Operons

In [5]:
## Fetching operon coordinates

with open("./list_of_operons.txt", mode="r") as outfile:
    lines = outfile.readlines()

def isnumber(x):
    try:
        x = int(x.strip())
        res = True
    except:
        res = False
    return res

lines = it.groupby(lines, lambda x: isnumber(x))
lines = [list(x[1]) for x in lines if x[0] == False]

operons = []
for oper in lines[1:]:
    start = int(oper[0].split()[3])
    end = int(oper[-1].split()[4])
    strand = oper[0].split()[5]
    desc = "; ".join([x.strip().split("\t")[6] for x in oper])
    operons.append((start, end, strand, desc))

print(lines[-1], operons[-3])

['\tAGNJBKDM_02609\tCDS\tROG1289\t2762267\t2762677\t-\tNA\n'] (2752627, 2757204, '+', 'NA; [E] Chorismate mutase; [R] Predicted periplasmic solute-binding protein; [G] 3-phosphoglycerate kinase; [R] Uncharacterized membrane protein (homolog of Drosophila; [S] Uncharacterized conserved protein')


In [6]:
## Fetching promoters

def reverse_complement(nsq):
    dct = {"A": "T", "T": "A", "G": "C", "C": "G"}
    out = []
    for nuc in reversed(nsq):
        out.append(dct[nuc])
    return "".join(out)

seq = []

with open("./c_limicola_genomic.fna", mode="r") as fasta:
    line = fasta.readline()
    for line in fasta:
        seq.append(line.strip())

seq = "".join(seq)

promoters = []
for start, end, strand, desc in operons:
    if strand == "+":
        promoters.append((desc, seq[start-151:start-1]))
    else:
        promoters.append((desc, reverse_complement(seq[end:end+150])))

print(promoters[0])

('[L] ATPase involved in DNA replication initiation; [L] DNA polymerase sliding clamp subunit (PCNA; [L] Recombinational DNA repair ATPase (RecF pathway); NA', 'TGTTGATAACCCAACAGGGACAGCTGCGGCTGATCTGTGGATTTTTCGGATGTTAAATTGTTTTTTATCCACCGAAAACTGTAACTTGTGAACATTCAATGTTGATGACTCTGTTCTTCCCCTCGTTTTTTTTACTAATTCTATGCCTGT')


In [49]:
## Promoters of operons containing housekeeping genes

keywords = ("ibosomal", "polymerase", "tRNA synthetase", "rRNA", "ATP synthase", "gyrase", "topoisomerase")

temp = tuple(promoters)
promoters = []

for prom in temp:
    desc = prom[0]
    household = False
    for word in keywords:
        if word in desc:
            household = True
    if household:
        promoters.append(prom)

In [7]:
## Printing to a file

with open("./household_promoters.fasta", mode="w") as fasta:
    i = 1
    for prom in promoters:
        print(f">promoter_{i} {prom[0]}", file=fasta)
        print(prom[1], file=fasta)
        i += 1

## MEME contest

In [60]:
with open("./memes/compare1.txt", mode="r") as outfile:
    motifs_1 = [(line.strip().split()[0], line.strip().split()[4]) for line in outfile.readlines()]

with open("./memes/compare2.txt", mode="r") as outfile:
    motifs_2 = [(line.strip().split()[0], line.strip().split()[4]) for line in outfile.readlines()]

motifs_1 = dict(motifs_1)

i = 0
for motif in motifs_2:
    if motif[0] in motifs_1.keys():
        if motif[1] in motifs_1.get(motif[0]):
            i += 1
            print(motif[0])

print("Длинных мотивов:", len(motifs_1))
print("Коротких мотивов:", len(motifs_2), "\n============================")
print("Короткий мотив внутри длинного:", i)

promoter_39
promoter_11
promoter_10
promoter_26
promoter_5
promoter_24
promoter_42
promoter_15
promoter_13
promoter_7
promoter_35
promoter_31
promoter_19
promoter_34
promoter_21
promoter_2
promoter_41
promoter_46
promoter_16
Длинных мотивов: 32
Коротких мотивов: 50 
Короткий мотив внутри длинного: 19


In [11]:
with open("./memes/compare1.txt", mode="r") as outfile:
    positions = [line.strip().split()[1] for line in outfile.readlines()]

for i in positions:
    print(i)

34
16
131
90
30
30
115
17
79
50
51
77
93
28
34
29
41
135
86
77
50
52
95
63
98
63
130
94
78
55
104
14


## Counting occurences

In [5]:
with open("fimo_neg.tsv", mode="r") as fimo:
    lines = fimo.readlines()[1:-4]

names = list(map(lambda x: x.split()[2], lines))
names = cl.Counter(names)

print("Промоторов:", len(names))
print("Находок:", sum(names.values()))

Промоторов: 179
Находок: 193
